In [ ]:
from google.colab import drive
drive.mount('/content/drive')
%cd /content/drive/MyDrive/

Mounted at /content/drive
/content/drive/MyDrive


In [ ]:
%pip install ultralytics transformers
import ultralytics
ultralytics.checks()

Ultralytics YOLOv8.2.32 🚀 Python-3.10.12 torch-2.3.0+cu121 CUDA:0 (NVIDIA L4, 22700MiB)
Setup complete ✅ (12 CPUs, 53.0 GB RAM, 30.2/201.2 GB disk)


In [ ]:
!pip install torch torchvision transformers segmentation-models-pytorch

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 106.7/106.7 kB 3.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.8/58.8 kB 9.7 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.2/2.2 MB 59.9 MB/s eta 0:00:00
  Created wheel for efficientnet-pytorch: filename=efficientnet_pytorch-0.7.1-py3-none-any.whl size=16429 sha256=ca2974fe62ba109d1bf3fc09bbb0828473913d2bd7a9c2e0c44387615dc54b9e
  Stored in directory: /root/.cache/pip/wheels/03/3f/e9/911b1bc46869644912bda90a56bcf7b960f20b5187feea3baf
  Created wheel for pretrainedmodels: filename=pretrainedmodels-0.7.4-py3-none-any.whl size=60945 sha256=72fc35d6f92682621c9b543427d59a0343ca1d8664073b4af5070d2d7e35cd1a
  Stored in directory: /root/.cache/pip/wheels/35/cb/a5/8f534c60142835bfc889f9a482e4a67e0b817032d9c6883b64
Successfully built efficientnet-pytorch pretrainedmodels


In [ ]:
%cd /content/drive/MyDrive/Projet Master 2024/Codes/semantic segmentation pytorch

/content/drive/.shortcut-targets-by-id/1FWKIhb94UOJewYN0A_2bgvf1zrl6eaDJ/Projet Master 2024/Codes/semantic segmentation pytorch


In [ ]:
import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import DataLoader, Dataset
from torchvision import transforms
from transformers import BertTokenizer, BertModel
from ultralytics import YOLO
from collections import defaultdict
from PIL import Image
from tqdm import tqdm
import json
import csv
import os
import segmentation_models_pytorch as smp
from utils.train import init_model, fit_model

In [ ]:
# Ensure CUDA (GPU support) is available if possible, else use CPU
device = 'cuda' if torch.cuda.is_available() else 'cpu'
print(f'Using device: {device}')

Using device: cuda


In [ ]:
os.environ['CUDA_VISIBLE_DEVICES'] = '0'

In [ ]:
# Load the trained YOLOv8 model
yolo_model = YOLO('/content/drive/MyDrive/00_PFE/Object_Detection/Training_Results/Yolov8-V6/Results/runs/train/experiment/weights/best.pt').to(device)

In [ ]:
class parse_args:
    dataset_name = 'FloodNet'
    classes = [
        'background', 'building-flooded', 'building-non-flooded',
        'road-flooded', 'road-non-flooded', 'water', 'tree',
        'vehicle', 'pool', 'grass'
    ]
    n_classes = len(classes)
    models_path = '/content/drive/MyDrive/Projet Master 2024/Codes/semantic segmentation pytorch/outputs'

    use_pretrained = False
    previous_epochs = 0
    attention_module = 'cbam_block'
    input_features = "RGB"
    model_architecture = "deeplabv3plus"
    batch_size = 32
    num_epochs = 50
    lr = 0.0001
    momentum = 0.9
    weight_decay = 1e-4
    power = 0.9
    crop_size = 256
    amp = False
    backbone = 'resnet50'
    encoder_weights = 'imagenet'
    num_workers = 8
    num_train_images = 100
    num_val_images = 10
    num_test_images = 10

    @property
    def model_save_path(self):
        return os.path.join(self.models_path, self.dataset_name, self.input_features, self.model_architecture)

    @property
    def device(self):
        return torch.device("cuda" if torch.cuda.is_available() else "cpu")

args = parse_args()
deeplab_model, criterion, optimizer, scheduler = init_model(args)
checkpoint_path = os.path.join(args.model_save_path, f'{args.model_architecture}_{args.backbone}.pth')

if os.path.exists(checkpoint_path):
    print(f"Loading model saved in the file: {checkpoint_path}")
    checkpoint = torch.load(checkpoint_path)
    deeplab_model.load_state_dict(checkpoint['model'])
else:
    print('Error: File does not exist.')

deeplab_model.eval()


Params: 40.3M
Error: File does not exist.


DataParallel(
  (module): DeepLabV3Plus(
    (backbone): ResNet(
      (conv1): Conv2d(3, 64, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3), bias=False)
      (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (relu): ReLU(inplace=True)
      (maxpool): MaxPool2d(kernel_size=3, stride=2, padding=1, dilation=1, ceil_mode=False)
      (layer1): Sequential(
        (0): Bottleneck(
          (conv1): Conv2d(64, 64, kernel_size=(1, 1), stride=(1, 1), bias=False)
          (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
          (conv2): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
          (bn2): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
          (conv3): Conv2d(64, 256, kernel_size=(1, 1), stride=(1, 1), bias=False)
          (bn3): BatchNorm2d(256, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
          (relu): Re

In [ ]:
# Define the label mapping
label_mapping = [
    "flooded", "non flooded", "flooded,non flooded", "Yes", "No",
    "0", "1", "2", "3", "4", "5", "6", "7", "8", "9",
    "10", "11", "12", "13", "14", "15", "16", "17", "18", "19",
    "20", "21", "22", "23", "24", "25", "26", "27", "28", "29",
    "30", "31", "32", "33", "34", "35", "36", "37", "38", "39",
    "40", "41", "42", "43", "44", "45", "46", "47", "48", "49", "50"
]

question_type_mapping = {
    "Condition_Recognition": 0,
    "Yes_No": 1,
    "Simple_Counting": 2,
    "Complex_Counting": 3
}

In [ ]:
# Function to extract features from YOLOv8
def extract_yolo_features(image_path, model, device):
    results = model(image_path)

    # Initialize lists to store extracted features
    boxes_list = []
    cls_list = []

    for result in results:
        if result.boxes is not None:
            boxes = result.boxes.xyxy.to(device)  # Bounding box coordinates
            classes = result.boxes.cls.to(device)  # Class values
            boxes_list.append(boxes)
            cls_list.append(classes)

    # Combine features into a single tensor
    if boxes_list:
        features = torch.cat([torch.cat(boxes_list), torch.cat(cls_list).unsqueeze(1)], dim=1)
    else:
        features = torch.empty((0, 5), device=device)

    return features

In [ ]:
# Function to extract features from DeepLabV3+
def extract_deeplab_features(image_path, model, device):
    image = Image.open(image_path).convert('RGB')
    transform = transforms.Compose([
        transforms.Resize((224, 224)),
        transforms.ToTensor()
    ])
    image = transform(image).unsqueeze(0).to(device)
    with torch.no_grad():
        if isinstance(model, torch.nn.DataParallel):
            model = model.module  # Unwrap the model if it's wrapped in DataParallel
        output = model(image)

        # Print the type and structure of the output
        print(f"Type of model output: {type(output)}")
        print(f"Output shape: {output.shape}")

        # Use the output tensor directly and reduce dimensions
        features = output

        print(f"Original DeepLab features shape: {features.shape}")

        # Reduce the dimensions
        features = nn.AdaptiveAvgPool2d((7, 7))(features)  # Reduce to (batch_size, 10, 7, 7)
        features = features.view(features.size(0), -1)  # Flatten the features to (batch_size, 10 * 7 * 7)

        print(f"Flattened DeepLab features shape: {features.shape}")

    return features

In [ ]:
# VQADataset class
class VQADataset(Dataset):
    def __init__(self, annotations_file, img_dir, tokenizer, transform=None):
        with open(annotations_file, 'r') as f:
            self.annotations = json.load(f)
        self.img_dir = img_dir
        self.transform = transform
        self.tokenizer = tokenizer
        self.img_to_annotations = self._group_by_image()

    def _group_by_image(self):
        img_to_annotations = defaultdict(list)
        for idx, annotation in self.annotations.items():
            img_to_annotations[annotation['Image_ID']].append(annotation)
        return img_to_annotations

    def __len__(self):
        return len(self.img_to_annotations)

    def __getitem__(self, idx):
        image_id = list(self.img_to_annotations.keys())[idx]
        annotations = self.img_to_annotations[image_id]
        img_path = os.path.join(self.img_dir, image_id)
        image = Image.open(img_path).convert('RGB')
        if self.transform:
            image = self.transform(image)
        questions = []
        answers = []
        question_types = []
        for annotation in annotations:
            inputs = self.tokenizer.encode_plus(
                annotation['Question'],
                add_special_tokens=True,
                return_tensors='pt',
                padding='max_length',
                truncation=True,
                max_length=64
            )
            question = inputs['input_ids'].squeeze(0).to(device)
            attention_mask = inputs['attention_mask'].squeeze(0).to(device)
            answer_text = str(annotation['Ground_Truth'])
            answer_idx = label_mapping.index(answer_text)
            question_type_idx = question_type_mapping[annotation['Question_Type']]
            questions.append((question, attention_mask))
            answers.append(torch.tensor(answer_idx, device=device))
            question_types.append(torch.tensor(question_type_idx, device=device))
        return {
            'image_path': img_path,
            'questions': questions,
            'attention_masks': [am for _, am in questions],
            'answers': torch.stack(answers),
            'question_types': torch.stack(question_types)
        }

In [ ]:
def custom_collate_fn(batch):
    batch_image_paths = [item['image_path'] for item in batch]
    batch_questions = [q for item in batch for q, _ in item['questions']]
    batch_attention_masks = [am for item in batch for _, am in item['questions']]
    batch_answers = torch.cat([item['answers'] for item in batch])
    batch_question_types = torch.cat([item['question_types'] for item in batch])
    num_questions_per_image = [len(item['questions']) for item in batch]
    return {
        'image_paths': batch_image_paths,
        'questions': batch_questions,
        'attention_masks': batch_attention_masks,
        'answers': batch_answers,
        'question_types': batch_question_types,
        'num_questions_per_image': num_questions_per_image
    }

In [ ]:
class VQAModel(nn.Module):
    def __init__(self, bert_model, yolo_input_dim, deeplab_input_dim, hidden_dim, combined_dim, vocab_size, num_question_types):
        super(VQAModel, self).__init__()
        self.bert_model = bert_model
        self.fc_yolo = nn.Linear(yolo_input_dim, hidden_dim)
        self.fc_deeplab = nn.Linear(deeplab_input_dim, hidden_dim)
        self.fc_question_type = nn.Embedding(num_question_types, hidden_dim)
        self.fc_proj = nn.Linear(hidden_dim * 3, combined_dim)  # Project to BERT input dimension

    def forward(self, yolo_features, deeplab_features, questions, attention_masks, question_types, num_questions_per_image):
        yolo_features = [self.fc_yolo(yolo_feature) for yolo_feature in yolo_features]
        yolo_features = torch.stack(yolo_features)

        deeplab_features = [self.fc_deeplab(deeplab_feature) for deeplab_feature in deeplab_features]
        deeplab_features = torch.stack(deeplab_features)

        text_features = [self.bert_model(question.unsqueeze(0).to(yolo_features.device), attention_mask=attention_mask.unsqueeze(0).to(yolo_features.device)).pooler_output for question, attention_mask in zip(questions, attention_masks)]
        text_features = torch.cat(text_features, dim=0)

        expanded_yolo_features = []
        expanded_deeplab_features = []
        for yolo_feature, deeplab_feature, num_questions in zip(yolo_features, deeplab_features, num_questions_per_image):
            expanded_yolo_features.append(yolo_feature.repeat(num_questions, 1))
            expanded_deeplab_features.append(deeplab_feature.repeat(num_questions, 1))
        expanded_yolo_features = torch.cat(expanded_yolo_features, dim=0)
        expanded_deeplab_features = torch.cat(expanded_deeplab_features, dim=0)

        question_type_features = self.fc_question_type(question_types)

        combined_features = torch.cat((expanded_yolo_features, expanded_deeplab_features, question_type_features), dim=1)

        projected_features = self.fc_proj(combined_features)

        # Reshape projected features to match BERT's expected input dimensions
        batch_size = projected_features.size(0)
        seq_length = 1  # Since we're treating each feature set as a single "sequence"
        projected_features = projected_features.view(batch_size, seq_length, -1)

        # Prepare BERT inputs
        extended_attention_mask = torch.ones((batch_size, seq_length), device=projected_features.device)

        # Pass through BERT model
        outputs = self.bert_model(inputs_embeds=projected_features, attention_mask=extended_attention_mask)
        pooled_output = outputs.pooler_output

        return pooled_output

In [ ]:
# Initialize tokenizer, BERT model, and VQA model
bert_tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
bert_model = BertModel.from_pretrained('bert-base-uncased').to(device)
num_classes = len(label_mapping)
num_question_types = len(question_type_mapping)
hidden_dim = 256
deeplab_input_dim = 10 * 7 * 7  # Adjust based on actual dimensions
combined_dim = 768  # Adjust based on BERT input dimensions
vqa_model = VQAModel(bert_model=bert_model, yolo_input_dim=5, deeplab_input_dim=deeplab_input_dim, hidden_dim=hidden_dim, combined_dim=combined_dim, vocab_size=num_classes, num_question_types=num_question_types).to(device)

In [ ]:
# Load the previous model
model_path = '/content/drive/MyDrive/00_PFE/VQA/Code-V6/VQAModel_Best.pth'
if os.path.exists(model_path):
    vqa_model.load_state_dict(torch.load(model_path))
    print("Loaded the previous model.")

Loaded the previous model.


In [ ]:
# Define optimizer and loss function
optimizer = torch.optim.Adam(vqa_model.parameters(), lr=0.00001)
criterion = torch.nn.CrossEntropyLoss()

In [ ]:
# Initialize dataset and dataloader
annotations_file = '/content/drive/MyDrive/00_PFE/DataSet/Visual_Question_Answering /FloodNet Challenge @ EARTHVISION 2021 - Track 2/Questions/Training Question.json'
img_dir = '/content/drive/MyDrive/00_PFE/DataSet/Visual_Question_Answering /FloodNet Challenge @ EARTHVISION 2021 - Track 2/Images/Train_Image'
transform = transforms.Compose([
    transforms.Resize((224, 224)),
    transforms.ToTensor()
])
dataset = VQADataset(annotations_file, img_dir, bert_tokenizer, transform)
dataloader = DataLoader(dataset, batch_size = 128, shuffle=True, collate_fn=custom_collate_fn)

In [ ]:
# Setup logging
def setup_logging():
    with open('/content/drive/MyDrive/00_PFE/VQA/Code-V6/log.csv', 'w', newline='') as file:
        writer = csv.writer(file)
        writer.writerow(["Epoch", "Average Loss", "Average Accuracy"])

def log_epoch(epoch, avg_loss, avg_accuracy):
    with open('/content/drive/MyDrive/00_PFE/VQA/Code-V6/log.csv', 'a', newline='') as file:
        writer = csv.writer(file)
        writer.writerow([epoch, f"{avg_loss:.4f}", f"{avg_accuracy * 100:.2f}%"])

In [ ]:
# Function to compute accuracy
def compute_accuracy(predictions, labels):
    _, predicted = torch.max(predictions, 1)
    correct = (predicted == labels).float().sum()
    return correct / labels.size(0)

In [ ]:
setup_logging()
num_epochs = 10
best_accuracy = 0.0

for epoch in range(num_epochs):
    total_loss = 0
    total_accuracy = 0
    total_batches = 0
    vqa_model.train()
    with tqdm(dataloader, desc=f"Epoch {epoch + 1}") as pbar:
        for batch in pbar:
            image_paths = batch['image_paths']
            questions = batch['questions']
            attention_masks = batch['attention_masks']
            answers = batch['answers']
            question_types = batch['question_types']
            num_questions_per_image = batch['num_questions_per_image']

            # Extract features using YOLOv8 and DeepLabV3+
            yolo_features_list = []
            deeplab_features_list = []
            for image_path in image_paths:
                yolo_features = extract_yolo_features(image_path, yolo_model, device)
                if yolo_features.nelement() == 0:
                    yolo_features = torch.zeros((1, 5), device=device)  # Handle no detections case
                yolo_features_list.append(yolo_features.mean(dim=0))

                deeplab_features = extract_deeplab_features(image_path, deeplab_model, device)
                if deeplab_features.nelement() == 0:
                    deeplab_features = torch.zeros((1, deeplab_input_dim), device=device)  # Handle no detections case
                deeplab_features_list.append(deeplab_features.mean(dim=0))

            yolo_features = torch.stack(yolo_features_list)
            deeplab_features = torch.stack(deeplab_features_list)

            print(f"YOLO features: {yolo_features.shape}")
            print(f"DeepLab features: {deeplab_features.shape}")

            optimizer.zero_grad()
            outputs = vqa_model(yolo_features, deeplab_features, questions, attention_masks, question_types, num_questions_per_image)
            loss = criterion(outputs, answers)
            if torch.isnan(loss):
                print(f"Encountered NaN loss, skipping this batch")
                continue
            loss.backward()
            optimizer.step()

            batch_loss = loss.item()
            batch_accuracy = compute_accuracy(outputs, answers).item()
            total_loss += batch_loss
            total_accuracy += batch_accuracy
            total_batches += 1
            pbar.set_postfix(Loss=batch_loss, Accuracy=f"{batch_accuracy:.4f}")

    avg_loss = total_loss / total_batches
    avg_accuracy = total_accuracy / total_batches
    print(f"Epoch {epoch + 1} - Average Loss: {avg_loss:.4f}, Average Accuracy: {avg_accuracy:.4f}")

    log_epoch(epoch + 1, avg_loss, avg_accuracy)

    # Save the best model
    if avg_accuracy > best_accuracy:
        best_accuracy = avg_accuracy
        torch.save(vqa_model.state_dict(), f"/content/drive/MyDrive/00_PFE/VQA/Code-V6/VQAModel_Best.pth")

print("Training complete!")

Epoch 1:   0%|          | 0/12 [00:00<?, ?it/s]


image 1/1 /content/drive/MyDrive/00_PFE/DataSet/Visual_Question_Answering /FloodNet Challenge @ EARTHVISION 2021 - Track 2/Images/Train_Image/6538.JPG: 480x640 (no detections), 9.3ms
Speed: 3.5ms preprocess, 9.3ms inference, 1.3ms postprocess per image at shape (1, 3, 480, 640)
Type of model output: <class 'torch.Tensor'>
Output shape: torch.Size([1, 10, 224, 224])
Original DeepLab features shape: torch.Size([1, 10, 224, 224])
Flattened DeepLab features shape: torch.Size([1, 490])

image 1/1 /content/drive/MyDrive/00_PFE/DataSet/Visual_Question_Answering /FloodNet Challenge @ EARTHVISION 2021 - Track 2/Images/Train_Image/6279.JPG: 480x640 1 Building-non-flooded, 7.7ms
Speed: 3.2ms preprocess, 7.7ms inference, 2.1ms postprocess per image at shape (1, 3, 480, 640)
Type of model output: <class 'torch.Tensor'>
Output shape: torch.Size([1, 10, 224, 224])
Original DeepLab features shape: torch.Size([1, 10, 224, 224])
Flattened DeepLab features shape: torch.Size([1, 490])

image 1/1 /content

Epoch 1:   8%|▊         | 1/12 [04:00<44:02, 240.24s/it, Accuracy=0.3387, Loss=4.85]


image 1/1 /content/drive/MyDrive/00_PFE/DataSet/Visual_Question_Answering /FloodNet Challenge @ EARTHVISION 2021 - Track 2/Images/Train_Image/9287.JPG: 480x640 1 Background, 4 Road-non-floodeds, 10.9ms
Speed: 3.6ms preprocess, 10.9ms inference, 3.0ms postprocess per image at shape (1, 3, 480, 640)
Type of model output: <class 'torch.Tensor'>
Output shape: torch.Size([1, 10, 224, 224])
Original DeepLab features shape: torch.Size([1, 10, 224, 224])
Flattened DeepLab features shape: torch.Size([1, 490])

image 1/1 /content/drive/MyDrive/00_PFE/DataSet/Visual_Question_Answering /FloodNet Challenge @ EARTHVISION 2021 - Track 2/Images/Train_Image/7061.JPG: 480x640 3 Road-non-floodeds, 7.8ms
Speed: 3.1ms preprocess, 7.8ms inference, 1.6ms postprocess per image at shape (1, 3, 480, 640)
Type of model output: <class 'torch.Tensor'>
Output shape: torch.Size([1, 10, 224, 224])
Original DeepLab features shape: torch.Size([1, 10, 224, 224])
Flattened DeepLab features shape: torch.Size([1, 490])

i

Epoch 1:  17%|█▋        | 2/12 [07:59<39:58, 239.80s/it, Accuracy=0.3622, Loss=4.85]

...


image 1/1 /content/drive/MyDrive/00_PFE/DataSet/Visual_Question_Answering /FloodNet Challenge @ EARTHVISION 2021 - Track 2/Images/Train_Image/7542.JPG: 448x640 3 Backgrounds, 29 Building-floodeds, 4 Road-floodeds, 9.3ms
Speed: 3.2ms preprocess, 9.3ms inference, 2.5ms postprocess per image at shape (1, 3, 448, 640)
Type of model output: <class 'torch.Tensor'>
Output shape: torch.Size([1, 10, 224, 224])
Original DeepLab features shape: torch.Size([1, 10, 224, 224])
Flattened DeepLab features shape: torch.Size([1, 490])

image 1/1 /content/drive/MyDrive/00_PFE/DataSet/Visual_Question_Answering /FloodNet Challenge @ EARTHVISION 2021 - Track 2/Images/Train_Image/10821.JPG: 448x640 (no detections), 7.8ms
Speed: 3.0ms preprocess, 7.8ms inference, 1.0ms postprocess per image at shape (1, 3, 448, 640)
Type of model output: <class 'torch.Tensor'>
Output shape: torch.Size([1, 10, 224, 224])
Original DeepLab features shape: torch.Size([1, 10, 224, 224])
Flattened DeepLab features shape: torch.Siz

Epoch 10:  92%|█████████▏| 11/12 [15:15<01:23, 83.15s/it, Accuracy=0.3174, Loss=4.82]


image 1/1 /content/drive/MyDrive/00_PFE/DataSet/Visual_Question_Answering /FloodNet Challenge @ EARTHVISION 2021 - Track 2/Images/Train_Image/8176.JPG: 480x640 1 Road-non-flooded, 7.9ms
Speed: 3.1ms preprocess, 7.9ms inference, 1.9ms postprocess per image at shape (1, 3, 480, 640)
Type of model output: <class 'torch.Tensor'>
Output shape: torch.Size([1, 10, 224, 224])
Original DeepLab features shape: torch.Size([1, 10, 224, 224])
Flattened DeepLab features shape: torch.Size([1, 490])

image 1/1 /content/drive/MyDrive/00_PFE/DataSet/Visual_Question_Answering /FloodNet Challenge @ EARTHVISION 2021 - Track 2/Images/Train_Image/8174.JPG: 480x640 1 Road-non-flooded, 8.0ms
Speed: 3.2ms preprocess, 8.0ms inference, 1.9ms postprocess per image at shape (1, 3, 480, 640)
Type of model output: <class 'torch.Tensor'>
Output shape: torch.Size([1, 10, 224, 224])
Original DeepLab features shape: torch.Size([1, 10, 224, 224])
Flattened DeepLab features shape: torch.Size([1, 490])

image 1/1 /content/

Epoch 10: 100%|██████████| 12/12 [15:41<00:00, 78.49s/it, Accuracy=0.3248, Loss=4.8]

Epoch 10 - Average Loss: 4.8341, Average Accuracy: 0.3283
Training complete!
